In [1]:
# import required packages
from oauth2client.client import OAuth2WebServerFlow
from googleapiclient.discovery import build
import httplib2

# Use Your Google Cloud Project Client ID & Client Secrets"
CLIENT_ID = "65916710692-nto9on46tma4r7vusuuscrk921a3mb70.apps.googleusercontent.com"
CLIENT_SECRET = "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"

# Define Oath scopes with read only access
OAUTH_SCOPE = "https://www.googleapis.com/auth/webmasters.readonly"

# OAUTH_SCOPE = "https://www.googleapis.com/auth/webmasters.readonly"

# Redirect URI to open Authorization Code Window in Browser
REDIRECT_URI = 'urn:ietf:wg:oauth:2.0:oob'

# Build URL that generates Authorization Code
flow = OAuth2WebServerFlow(CLIENT_ID, CLIENT_SECRET, OAUTH_SCOPE, REDIRECT_URI)
authorize_url = flow.step1_get_authorize_url()

# Print Authorization Command
print("Go to the following link in your browser: " + authorize_url)
auth_code = input("Enter your Authorization Code here: ")
# Get Credentials to build gsc API service
credentials = flow.step2_exchange(auth_code)
print("The Credentials are Generated Successfully")
# create httplib2.Http object and authorize it with ouy credentials
http = httplib2.Http()
# authorize credentials
creds = credentials.authorize(http)
# building a service to access various features of GSC API
webmasters_service = build('searchconsole', 'v1', http=creds )

__init__() takes at most 4 positional arguments (5 given)


Go to the following link in your browser: https://accounts.google.com/o/oauth2/v2/auth?client_id=65916710692-nto9on46tma4r7vusuuscrk921a3mb70.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fwebmasters.readonly&access_type=offline&response_type=code
The Credentials are Generated Successfully


# How to get a list of sites we have in GSC account?

In [2]:
# get a list of site in google search console account
site_list = webmasters_service.sites().list().execute()
print(site_list)

{'siteEntry': [{'siteUrl': 'sc-domain:bizben.com', 'permissionLevel': 'siteUnverifiedUser'}, {'siteUrl': 'https://www.bizben.com/', 'permissionLevel': 'siteFullUser'}]}


# How to get Google Search Console Analytics Data?

In [21]:
#the website we want to get the data for
website = "https://www.bizben.com/"

#build a request body
request_body = {
    "startDate" : '2024-12-13',
    "endDate" : '2025-01-13',
    "dimensions" : ['QUERY','PAGE'],
    "rowLimit": 25000,
    "dataState" : "final"
}

#get the response body
response_data = webmasters_service.searchanalytics().query(siteUrl=website, body=request_body).execute()

In [22]:
len(response_data['rows'])

25000

In [23]:
for each in response_data['rows']:
    print(each)

{'keys': ['bizben', 'https://www.bizben.com/'], 'clicks': 1509, 'impressions': 2211, 'ctr': 0.6824966078697422, 'position': 1.0009045680687472}
{'keys': ['gas station for sale in california', 'https://www.bizben.com/business-for-sale/gas-stations-for-sale-type-california-ca.php'], 'clicks': 220, 'impressions': 1066, 'ctr': 0.20637898686679174, 'position': 3.547842401500938}
{'keys': ['liquor store for sale in california', 'https://www.bizben.com/business-for-sale/liquor-stores-for-sale-type-california-ca.php'], 'clicks': 155, 'impressions': 553, 'ctr': 0.28028933092224234, 'position': 1.379746835443038}
{'keys': ['laundromat for sale san diego', 'https://www.bizben.com/business-for-sale/coin-laundry-for-sale-san-diego-california-203955.php'], 'clicks': 142, 'impressions': 801, 'ctr': 0.1772784019975031, 'position': 2.937578027465668}
{'keys': ['laundromat for sale', 'https://www.bizben.com/business-for-sale/laundromat-for-sale-los-angeles-county-california-204592.php'], 'clicks': 123, 

How to use While Loop to Extract more than 25,000 rows

In [36]:
# while the response has 25000 rows of data, then keep making gsc call

# create an empty list to store the rows from response
all_responses = []

# define a startRow
startRow = 0

while (startRow == 0) or (startRow%25000 == 0):
  # build a request body
  request_body = {
      "startDate"	: '2024-12-13',
      "endDate" : '2025-01-13',
      "dimensions" : ['QUERY','PAGE'],
      "rowLimit" : 25000,
      "dataState" : "final",
      'startRow' : startRow
      }

  #get gsc response
  response_data = webmasters_service.searchanalytics().query(siteUrl=website, body=request_body).execute()

  #update the rows
  startRow = startRow + len(response_data['rows'])
  print("fetched up to " + str(startRow) + " rows of data")

  # for loop tos save all the rows in all_responses
  for row in response_data['rows']:
    all_responses.append(row)


fetched up to 25000 rows of data
fetched up to 50000 rows of data
fetched up to 75000 rows of data
fetched up to 100000 rows of data
fetched up to 125000 rows of data
fetched up to 150000 rows of data
fetched up to 175000 rows of data
fetched up to 193811 rows of data


In [37]:
len(all_responses)

193811

In [38]:
all_responses[0]

{'keys': ['bizben', 'https://www.bizben.com/'],
 'clicks': 1509,
 'impressions': 2211,
 'ctr': 0.6824966078697422,
 'position': 1.0009045680687472}

Build a Data Frames Using Pandas

In [39]:
#empty list to build a dataframe
data_for_df = []

for each in all_responses:

  temp = []
  #query
  temp.append(each['keys'][0])

  #page
  temp.append(each['keys'][1])

  #clicks
  temp.append(each['clicks'])

  #impressions
  temp.append(each['impressions'])

  #ctr
  temp.append(each['ctr'])

  #position
  temp.append(each['position'])

  data_for_df.append(temp)

In [40]:
data_for_df[0]

['bizben',
 'https://www.bizben.com/',
 1509,
 2211,
 0.6824966078697422,
 1.0009045680687472]

In [41]:
import pandas as pd

In [42]:
df = pd.DataFrame(data_for_df, columns=['query', 'page', 'clicks', 'impressions', 'ctr', 'position'])

In [43]:
df

query  \
0                                    bizben   
1        gas station for sale in california   
2       liquor store for sale in california   
3             laundromat for sale san diego   
4                       laundromat for sale   
...                                     ...   
193806                                بزبين   
193807                                بزبين   
193808                                 بسنس   
193809                          مطاعم للبيع   
193810                          مطاعم للبيع   

                                                     page  clicks  \
0                                 https://www.bizben.com/    1509   
1       https://www.bizben.com/business-for-sale/gas-s...     220   
2       https://www.bizben.com/business-for-sale/liquo...     155   
3       https://www.bizben.com/business-for-sale/coin-...     142   
4       https://www.bizben.com/business-for-sale/laund...     123   
...                                                   ...     ...   
193806  https://www.bizben.com/search-by-category-type...       0   
193807  https://www.bizben.com/search-by-state-county-...       0   
193808                            https://www.bizben.com/       0   
193809  https://www.bizben.com/business-for-sale/resta...       0   
193810  https://www.bizben.com/business-for-sale/resta...       0   

        impressions       ctr   position  
0              2211  0.682497   1.000905  
1              1066  0.206379   3.547842  
2               553  0.280289   1.379747  
3               801  0.177278   2.937578  
4              2482  0.049557   6.448832  
...             ...       ...        ...  
193806            6  0.000000   1.500000  
193807           10  0.000000   1.500000  
193808            1  0.000000  72.000000  
193809            1  0.000000   3.000000  
193810            1  0.000000   5.000000  

[193811 rows x 6 columns]

# Export to CSV or Excel

In [44]:
df.to_excel('data.xlsx')

C:\Users\elija\AppData\Roaming\Python\Python311\site-packages\xlsxwriter\worksheet.py:1261: UserWarning: Ignoring URL 'https://www.bizben.com/business-for-sale/coldstone-creamery-franchise-for-sale-mountain-view-california-ca-167535.php' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  warn(
C:\Users\elija\AppData\Roaming\Python\Python311\site-packages\xlsxwriter\worksheet.py:1261: UserWarning: Ignoring URL 'https://www.bizben.com/business-for-sale/san-francisco-bay-area-cold-stone-creamery-for-sale-203954.php' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  warn(
C:\Users\elija\AppData\Roaming\Python\Python311\site-packages\xlsxwriter\worksheet.py:1261: UserWarning: Ignoring URL 'https://www.bizben.com/business-for-sale/cold-stone-creamery-for-sale-in-sonoma-county-california-281224.php' since it exceeds Excel's limit of 65,530 URLS per worksheet.
  warn(
C:\Users\elija\AppData\Roaming\Python\Python311\site-packages\xlsxwriter\worksheet.py:1261: UserWarnin

In [35]:
df.to_csv('data.csv')

# How to use Dimensions and Dimension Groups


In [ ]:
# create an empty list to store the rows from response
all_responses = []

# define a startRow
startRow = 0

while (startRow == 0) or (startRow%25000 == 0):
  # build a request body
  request_body = {
      "startDate"	: '2023-01-01',
      "endDate" : '2023-01-02',
      "dimensions" : ['DATE', 'QUERY', 'PAGE', 'COUNTRY', 'DEVICE'],
      "dimensionFilterGroups": [ { "filters": [
                  {"dimension": "QUERY", "expression": "python", "operator": "notContains" },
                  {"dimension": "PAGE", "expression": "python", "operator": "contains" },
                  {"dimension": "COUNTRY", "expression": "USA", "operator": "equals" }
                  ]}],
      "rowLimit" : 25000,
      "dataState" : "final",
      'startRow' : startRow
      }

  #get gsc response
  response_data = webmasters_service.searchanalytics().query(siteUrl=website, body=request_body).execute()

  #update the rows
  startRow = startRow + len(response_data['rows'])
  print("fetched up to " + str(startRow) + " rows of data")

  # for loop tos save all the rows in all_responses
  for row in response_data['rows']:
    all_responses.append(row)

KeyError: 'rows'

In [ ]:
all_responses[0]
